
### Transform and Export Processed Data to ADLS 

Extract data from imported database assuming default Access NI schema.
Data is converted to flat denormalized CSV files and exported to ADLS **silver** container.

One CSV file will be created for each Sequence File name that was called.


In [0]:
# Declare script variables
debug_mode = True
database_name = "dbo"

bronze_source = "abfss://bronze@arcdatalakeg2.dfs.core.windows.net/"
bronze_target = bronze_source + database_name
bronze_mnt = "/mnt/bronze/" + database_name

silver_source = "abfss://silver@arcdatalakeg2.dfs.core.windows.net/"
silver_target = silver_source + database_name
silver_mnt = "/mnt/silver/" + database_name

gold_source = "abfss://gold@arcdatalakeg2.dfs.core.windows.net/"
gold_target = gold_source + database_name
gold_mnt = "/mnt/gold/" + database_name

In [0]:
# Get all desired test runs

sql_string_crosstab = f"""
    SELECT  STEP_SEQCALL.SEQUENCE_FILE_PATH,
            UUT_RESULT.ID,
            UUT_RESULT.START_DATE_TIME, 
            UUT_RESULT.STATION_ID, 
            UUT_RESULT.UUT_SERIAL_NUMBER,
            CAST(UUT_RESULT.TEST_SOCKET_INDEX AS INT), 
            UUT_RESULT.UUT_STATUS, 
            CAST(UUT_RESULT.EXECUTION_TIME AS INT),
            STEP_RESULT.STEP_NAME, 
            ROUND(CAST(PROP_RESULT.DATA AS DOUBLE), 3)
    FROM UUT_RESULT LEFT JOIN STEP_RESULT 
        ON UUT_RESULT.ID = STEP_RESULT.UUT_RESULT
            LEFT JOIN PROP_RESULT 
                ON STEP_RESULT.ID = PROP_RESULT.STEP_RESULT
                    LEFT JOIN STEP_SEQCALL 
                        ON STEP_SEQCALL.STEP_RESULT = STEP_RESULT.STEP_PARENT
    WHERE UUT_STATUS <> 'Terminated' 
        and UUT_STATUS <> 'Error' 
        and STATION_ID is not NULL
        and STEP_RESULT.STEP_TYPE = 'NumericLimitTest'   
        and PROP_RESULT.TYPE_NAME = 'NumericLimitTest'
    ORDER BY START_DATE_TIME, TEST_SOCKET_INDEX, STEP_RESULT.ORDER_NUMBER ASC
    """

test_results = spark.sql(sql_string_crosstab)

display(test_results)

SEQUENCE_FILE_PATH ID START_DATE_TIME STATION_ID UUT_SERIAL_NUMBER TEST_SOCKET_INDEX UUT_STATUS EXECUTION_TIME STEP_NAME round(CAST(DATA AS DOUBLE), 3) C:\Program Files (x86)\MKS\352 Final Test\seqs\352021.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Apply DUT Power 0.328 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 9.9E37 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate DeviceNet Resistance 13960.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify VAC Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify ATM Pressure 3590.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify VAC Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify ATM Pressure 3590.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify VAC Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify ATM Pressure 3589.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify CG Pressure 2804.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify CG Pressure 2805.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Verify CG Pressure 2805.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Test\seqs\Common.seq 2 2021-11-10 15:00:30.0000000 BRM-DQ1VH63 352C0000 -1 Passed 545 Evaluate Pressure 0.0 C:\Program Files (x86)\MKS\352 Final Te